In [3]:
using LinearAlgebra
using Distributed
using SharedArrays
using Plots
using DataFrames, CSV
using Revise

In [4]:
using BeyondHulten

## Loading in Data

In [5]:
data = read_data("I-O_DE2019_formatiert.csv")

CESData(84×87 DataFrame
 Row │ Sektoren                           Erz. d. Landwirtschaft, Jagd und Die ⋯
     │ String                             Int64                                ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ Erz. d. Landwirtschaft, Jagd und…                                       ⋯
   2 │ Forstwirtschaftl. Erzeugnisse un…
   3 │ Fische, Fischerei- und Aquakultu…
   4 │ Kohle
   5 │ Erdöl und Erdgas                                                        ⋯
   6 │ Erze, Steine und Erden, sonstige…
   7 │ Nahrungs- u. Futtermittel, Geträ…
   8 │ Textilien, Bekleidung, Leder und…
  ⋮  │                 ⋮                                          ⋮            ⋱
  78 │ Bruttolöhne und -gehälter                                               ⋯
  79 │ Sonst.Produktionsabgaben abzgl. …
  80 │ Abschreibungen
  81 │ Nettobetriebsüberschuss
  82 │ Bruttowertschöpfung                                                     ⋯
  83 │ Produktio

## Setting Elasticities

Es können verschiedene Elastizitäten gesetzt werden, die hier verwendeten sind übernommen aus B&F 2019 
(el. of substitiution of inermediates = 0.0001, el labor/intermediates  = 0.5 el. of consumption = 0.9)

In [6]:
elasticities = CESELasticities(0.001,0.5,0.9)

CESELasticities(0.001, 0.5, 0.9)

## Setting Shocks

Shocks können entweder mit `calculate_investment!` in  1000€ eingegeben werden, oder die einzelnen Elemente im Vektor können auch direkt verändernt werden (z.b `supply_shock[12] = 1.2`), was dann einem Anstieg an demand von 20% entsrpicht.

In [14]:
demand_shock = ones(71)
supply_shock = ones(71)
shocks = Shocks(supply_shock, demand_shock)
shocks.supply_shock[1] = 0.9
#sector = ["Vorb.Baustellen-,Bauinstallations-,Ausbauarbeiten"]
#investment = [25000]
#calculate_investment!(shocks, data, investment, sector)

0.9

## Full labor reallocation

In [15]:
solution = solve_ces_model(data, shocks, elasticities)

71×7 DataFrame
 Row │ prices    quantities   sectors                            value_added_a ⋯
     │ Float64   Float64      String                             Float64       ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 1.26767   0.0166847    Erz. d. Landwirtschaft, Jagd und…           107. ⋯
   2 │ 0.997821  0.00221356   Forstwirtschaftl. Erzeugnisse un…             4.
   3 │ 1.01416   0.00016062   Fische, Fischerei- und Aquakultu…             0.
   4 │ 0.998026  0.000964668  Kohle                                         0.
   5 │ 0.998015  0.000486604  Erdöl und Erdgas                              0. ⋯
   6 │ 0.997679  0.00467057   Erze, Steine und Erden, sonstige…             7.
   7 │ 1.03828   0.0646527    Nahrungs- u. Futtermittel, Geträ…           601.
   8 │ 0.993502  0.00742362   Textilien, Bekleidung, Leder und…            14.
  ⋮  │    ⋮           ⋮                       ⋮                           ⋮    ⋱
  65 │ 0.997242  0.0776392    Dienstleistungen des Gesundheits…          8459. ⋯
  66 │ 0.99723   0.0349536    Dienstleistungen von Heimen und …          1569.
  67 │ 0.997154  0.0113832    Dienstleist. der Kunst, Kultur u…           162.
  68 │ 0.997714  0.00980877   DL des Sports, der Unterhaltung …           102.
  69 │ 0.998442  0.0143477    DL d. Interessenvertr., kirchl. …           320. ⋯
  70 │ 0.99713   0.00143466   Reparaturarbeiten an DV-Geräten …             2.
  71 │ 0.997048  0.0178858    Sonstige überwiegend persönliche…           448.
                                                   4 columns and 56 rows omitted

In [16]:
println("Real GDP: $(real_gdp(solution,relative=true))")
println("Nominal GDP: $(nominal_gdp(solution,relative=true))")


Real GDP: 0.9982621561985534
Nominal GDP: 0.9979648301377121


## No labor reallocation 

Es können verschiedene Funktionen angegeben werden,die zurückgeben wie viel Arbeit in den einzelnen Sektoren verfügbar. Hier in diesem Fall, ist keine zusätzliche Arbeit verfügbar, die funktion könnte aber auch zum Beispiel so aussehen: 
```julia
labor_realloc(data) = min(1.05 * data.labor_share,inv(I - diagm(1 .- data.factor_share) * data.Ω) * (data.consumption_share_gross_output .* ((data.shocks.demand_shock .* data.labor_share) - data.labor_share)) + data.labor_share)
``` 
(maximal 5% der verfügbaren Arbeit kann zusätzlich verwendet werden um der gesteigerten Nachfrage nachzukommen)

In [14]:
labor_realloc(data) = data.labor_share #no labor_reallocation

┌ Error: Failed to revise /home/franzs/Schreibtisch/BeyondHulten/src/cobbdouglas.jl
│   exception = Revise.ReviseEvalException("/home/franzs/Schreibtisch/BeyondHulten/src/cobbdouglas.jl:1", UndefVarError(:Elasticities), Any[(top-level scope at cobbdouglas.jl:1, 1)])
└ @ Revise /home/franzs/.julia/packages/Revise/sCmwS/src/packagedef.jl:722


labor_realloc (generic function with 1 method)

In [15]:
sol = solve_ces_model(data, shocks, elasticities, labor_reallocation=labor_realloc)

71×7 DataFrame
 Row │ prices    quantities   sectors                            value_added_a ⋯
     │ Float64   Float64      String                             Float64       ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.921147  0.0176821    Erz. d. Landwirtschaft, Jagd und…           108. ⋯
   2 │ 0.927059  0.00220786   Forstwirtschaftl. Erzeugnisse un…             4.
   3 │ 0.921449  0.000162028  Fische, Fischerei- und Aquakultu…             0.
   4 │ 0.924777  0.000967106  Kohle                                         0.
   5 │ 0.920709  0.000486442  Erdöl und Erdgas                              0. ⋯
   6 │ 0.92793   0.00466287   Erze, Steine und Erden, sonstige…             7.
   7 │ 0.921786  0.0639388    Nahrungs- u. Futtermittel, Geträ…           588.
   8 │ 0.920675  0.00743283   Textilien, Bekleidung, Leder und…            14.
  ⋮  │    ⋮           ⋮                       ⋮                           ⋮    ⋱
  65 │ 0.920879  0.0776395    Dienstleistungen des Gesundheits…          8460. ⋯
  66 │ 0.922502  0.0349536    Dienstleistungen von Heimen und …          1569.
  67 │ 0.922771  0.0113844    Dienstleist. der Kunst, Kultur u…           162.
  68 │ 0.921322  0.00980525   DL des Sports, der Unterhaltung …           102.
  69 │ 0.924023  0.0143401    DL d. Interessenvertr., kirchl. …           320. ⋯
  70 │ 0.920789  0.00143414   Reparaturarbeiten an DV-Geräten …             2.
  71 │ 0.920507  0.0178855    Sonstige überwiegend persönliche…           448.
                                                   4 columns and 56 rows omitted

In [16]:
println("Real GDP: $(real_gdp(sol,relative=false))")
println("Nominal GDP: $(nominal_gdp(sol,relative=false))")

Real GDP: 110446.92349465049
Nominal GDP: 102575.53804978589


## Progressive Sector Shocks
Shock every sector and look at difference in impacts (output see the 4 demand_shock csv files: nominal, real, labor reallocation, no labor reallocation):

Sets the amount and range of shocks

In [17]:
min_shock = 1.0
max_shock = 1.8
shock_count = 50

50

Shocks each sector from `min_shock` to `max_shock` in `amount` stepsand returns a matrix containing the resulting GDP of each shock

In [18]:
function progressive_shocks(data, min_shock, max_shock, amount, GDP_function, labor_reallocation_function)
    GDP = SharedArray(zeros(length(data.labor_share), amount))
    shock_values = LinRange(min_shock, max_shock, amount)
    supply_shock = SharedArray(ones(71))


    @distributed for i in 1:71
        init = Complex.([ones(71)..., data.λ...])
        demand_shock = ones(71)
        for (k, shock_value) in enumerate(shock_values)
            demand_shock[i] = shock_value
            shock = Shocks(supply_shock, demand_shock)

            sol = solve_ces_model(data, shock, elasticities, init=init, labor_reallocation=labor_reallocation_function)
            GDP[i, k] = GDP_function(sol)
            #take solutions from before as init values, since solution from next run should be close 
            # to soultion from previous (comlex turns the real values back into complex number to allow for solution)
            init = Complex.([sol.prices..., sol.quantities...])
        end
    end
    return GDP
end

progressive_shocks (generic function with 1 method)

In [19]:
GDP_nominal = progressive_shocks(data, min_shock, max_shock, shock_count, nominal_gdp, full_demand_labor_allocation)
GDP_no_realloc_nominal = progressive_shocks(data, min_shock, max_shock, shock_count, nominal_gdp, labor_realloc)
GDP = progressive_shocks(data, min_shock, max_shock, shock_count, real_gdp, full_demand_labor_allocation)
GDP_no_realloc = progressive_shocks(data, min_shock, max_shock, shock_count, real_gdp, labor_realloc)

Saves the caluclated results as CSV. Each Row contains the effect on GDP, when shocking a sector from 1.0 to 1.8 

In [14]:
function savetabular(filname, gdp)
    sectors = data.io.Sektoren[1:71]
    df = DataFrame(gdp[1:end, :]', sectors)
    df[:, :DemandShockAmount] = collect(LinRange(min_shock, max_shock, shock_count))
    CSV.write(joinpath(pwd(), "data", filname), df)
end

savetabular (generic function with 1 method)

In [15]:

savetabular("demand_shock_nominal.csv", GDP_nominal)
savetabular("demand_shock_nominal_no_realloc.csv", GDP_no_realloc_nominal)
savetabular("demand_shock.csv", GDP)
savetabular("demand_shock_no_realloc.csv", GDP_no_realloc)

"/home/franzs/Schreibtisch/BeyondHulten/data/demand_shock_no_realloc.csv"

In [16]:
GDP_no_realloc_nominal

71×50 SharedMatrix{Float64}:
 1.0  0.999001  0.998002  0.997004  0.996006  …  0.953494  0.952516  0.951539
 1.0  0.999789  0.999578  0.999367  0.999155     0.989882  0.989663  0.989444
 1.0  0.999989  0.999978  0.999968  0.999957     0.999486  0.999475  0.999463
 1.0  0.999923  0.999845  0.999768  0.999691     0.996322  0.996242  0.996163
 1.0  0.999949  0.999897  0.999846  0.999795     0.997543  0.99749   0.997437
 1.0  0.999668  0.999337  0.999005  0.998673  …  0.984331  0.983996  0.983661
 1.0  0.998699  0.9974    0.996102  0.994805     0.940286  0.939048  0.93781
 1.0  0.999773  0.999546  0.999319  0.999091     0.989194  0.988961  0.988729
 1.0  0.99965   0.999299  0.998948  0.998598     0.983491  0.983139  0.982788
 1.0  0.999102  0.998204  0.997306  0.996409     0.958102  0.957219  0.956336
 ⋮                                            ⋱                      
 1.0  0.998528  0.997057  0.995586  0.994116     0.931667  0.930238  0.92881
 1.0  0.992878  0.985801  0.978768  0.97178  

In [17]:
l = @layout [a b; c d]

p1 = Plots.scatter(LinRange(min_shock, max_shock, shock_count), eachrow(GDP), labels="", title="GDP")
p2 = Plots.scatter(LinRange(min_shock, max_shock, shock_count), eachrow(GDP_no_realloc), labels="", title="no labor realloc")
p3 = Plots.scatter(LinRange(min_shock, max_shock, shock_count), eachrow(GDP_nominal), labels="", title="nominal")
p4 = Plots.scatter(LinRange(min_shock, max_shock, shock_count), eachrow(GDP_no_realloc_nominal), labels="", title="nominal no realloc")
Plots.plot(p1, p2, p3, p4, layout=l)

## Wertschöpfung pro Sektor

In [18]:
# Sample shock
demand_shock = ones(71)
supply_shock = ones(71)
shocks = Shocks(supply_shock, demand_shock)
#shocks.demand_shock[35] = 1.09
sector = ["Vorb.Baustellen-,Bauinstallations-,Ausbauarbeiten", "Keramik, bearbeitete Steine und Erden"]
investment = [25000, 1000]
#sector = ["Vorb.Baustellen-,Bauinstallations-,Ausbauarbeiten"]
#investment = [25000]
calculate_investment!(shocks, data, investment, sector)

Demand shock to sector Vorb.Baustellen-,Bauinstallations-,Ausbauarbeiten: 1.2048978788971576
Demand shock to sector Keramik, bearbeitete Steine und Erden: 1.087237197941202


In [19]:
sol = solve_ces_model(data, shocks, elasticities)

71×7 DataFrame
 Row │ prices    quantities   sectors                            value_added_a ⋯
     │ Float64   Float64      String                             Float64       ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 0.93674   0.0178239    Erz. d. Landwirtschaft, Jagd und…          109.6 ⋯
   2 │ 0.682092  0.00269826   Forstwirtschaftl. Erzeugnisse un…            5.4
   3 │ 0.620716  0.000192445  Fische, Fischerei- und Aquakultu…            0.0
   4 │ 0.792567  0.00104982   Kohle                                        0.4
   5 │ 0.71987   0.000571706  Erdöl und Erdgas                             0.2 ⋯
   6 │ 0.791021  0.00505727   Erze, Steine und Erden, sonstige…            7.0
   7 │ 0.936574  0.0645862    Nahrungs- u. Futtermittel, Geträ…          598.1
   8 │ 0.835826  0.00763614   Textilien, Bekleidung, Leder und…           13.8
  ⋮  │    ⋮           ⋮                       ⋮                           ⋮    ⋱
  65 │ 0.94001   0.0776253    Dienstleistungen des Gesundheits…         8456.2 ⋯
  66 │ 0.952488  0.0349536    Dienstleistungen von Heimen und …         1569.2
  67 │ 0.933726  0.0114287    Dienstleist. der Kunst, Kultur u…          163.7
  68 │ 0.930981  0.00985912   DL des Sports, der Unterhaltung …          102.9
  69 │ 0.922085  0.0145167    DL d. Interessenvertr., kirchl. …          324.3 ⋯
  70 │ 0.8602    0.00151411   Reparaturarbeiten an DV-Geräten …            2.7
  71 │ 0.933029  0.0179306    Sonstige überwiegend persönliche…          450.1
                                                   4 columns and 56 rows omitted

value_added is a a 71 element vector, whos i-th element is the value added in sector i

Look at sectoral value added:

In [20]:
print(sol[:, ["value_added_nominal_relative", "value_added_relative"]] .- data.labor_share)

71×2 DataFrame
 Row │ value_added_nominal_relative  value_added_relative 
     │ Float64                       Float64              
─────┼────────────────────────────────────────────────────
   1 │                 -0.000333858           4.8301e-5
   2 │                 -0.000234948           0.000227712
   3 │                 -3.06565e-5           -1.2256e-5
   4 │                 -9.13811e-5           -1.1916e-5
   5 │                 -6.31534e-5            1.66305e-5
   6 │                 -0.000351975          -3.60035e-5
   7 │                 -0.0007148             0.00018244
   8 │                 -0.000412664          -6.75738e-5
   9 │                 -0.000884057          -0.000390986
  10 │                 -0.000323497           1.4253e-5
  11 │                 -0.000194905           7.45151e-6
  12 │                 -0.00030366           -0.000235123
  13 │                 -0.00109128            0.000159351
  14 │                  1.34639e-5            4.68817e-5
  15 │    

Calculate inflation via GDP deflator:

In [21]:
deflator = sum(sol.value_added_nominal_relative) / sum(sol.value_added_relative)
println("GDP deflator: $(deflator)")
inflation_rate = (deflator - 1) / 1 #since initially the GDP deflator is 1 as we use pre-shock prices for value added and value added nominal
println("inflation rate: $(inflation_rate)")

GDP deflator: 0.9292432736667683
inflation rate: -0.07075672633323171


In [22]:
bar(1:71, [sol.value_added_relative - data.labor_share, sol.value_added_nominal_relative - data.labor_share], label=["Bar 1" "Bar 2"])

In [23]:
#TODO:
# BIP IN €
# GLEICH NACH BERECHNUNG ZURÜCKGEBEN
# ALS DATAFRAME
# Balken nebeinander
